# In this Analysis, you will be predicting the cumulative number of confirmed COVID19 cases in various locations across the world, as well as the number of resulting fatalities, for future dates.

In [ ]:
import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

In [125]:
train=pd.read_csv(r'C:\Users\SAYAN\Desktop\train.csv')
test=pd.read_csv(r'C:\Users\SAYAN\Desktop\test.csv')
g=train

In [126]:
train

Id Province_State Country_Region        Date  ConfirmedCases  \
0          1            NaN    Afghanistan  2020-01-22             0.0   
1          2            NaN    Afghanistan  2020-01-23             0.0   
2          3            NaN    Afghanistan  2020-01-24             0.0   
3          4            NaN    Afghanistan  2020-01-25             0.0   
4          5            NaN    Afghanistan  2020-01-26             0.0   
...      ...            ...            ...         ...             ...   
35990  35991            NaN       Zimbabwe  2020-05-11            36.0   
35991  35992            NaN       Zimbabwe  2020-05-12            36.0   
35992  35993            NaN       Zimbabwe  2020-05-13            37.0   
35993  35994            NaN       Zimbabwe  2020-05-14            37.0   
35994  35995            NaN       Zimbabwe  2020-05-15            42.0   

       Fatalities  
0             0.0  
1             0.0  
2             0.0  
3             0.0  
4             0.0  
...           ...  
35990         4.0  
35991         4.0  
35992         4.0  
35993         4.0  
35994         4.0  

[35995 rows x 6 columns]

In [127]:
test

ForecastId Province_State Country_Region        Date
0               1            NaN    Afghanistan  2020-04-02
1               2            NaN    Afghanistan  2020-04-03
2               3            NaN    Afghanistan  2020-04-04
3               4            NaN    Afghanistan  2020-04-05
4               5            NaN    Afghanistan  2020-04-06
...           ...            ...            ...         ...
13454       13455            NaN       Zimbabwe  2020-05-10
13455       13456            NaN       Zimbabwe  2020-05-11
13456       13457            NaN       Zimbabwe  2020-05-12
13457       13458            NaN       Zimbabwe  2020-05-13
13458       13459            NaN       Zimbabwe  2020-05-14

[13459 rows x 4 columns]

In [128]:
train.head()

Id Province_State Country_Region        Date  ConfirmedCases  Fatalities
0   1            NaN    Afghanistan  2020-01-22             0.0         0.0
1   2            NaN    Afghanistan  2020-01-23             0.0         0.0
2   3            NaN    Afghanistan  2020-01-24             0.0         0.0
3   4            NaN    Afghanistan  2020-01-25             0.0         0.0
4   5            NaN    Afghanistan  2020-01-26             0.0         0.0

In [129]:
train.shape

(35995, 6)

In [130]:
test.shape

(13459, 4)

In [131]:
train.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 35995 entries, 0 to 35994
Data columns (total 6 columns):
 #   Column          Non-Null Count  Dtype  
---  ------          --------------  -----  
 0   Id              35995 non-null  int64  
 1   Province_State  15295 non-null  object 
 2   Country_Region  35995 non-null  object 
 3   Date            35995 non-null  object 
 4   ConfirmedCases  35995 non-null  float64
 5   Fatalities      35995 non-null  float64
dtypes: float64(2), int64(1), object(3)
memory usage: 1.6+ MB


In [132]:
test.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 13459 entries, 0 to 13458
Data columns (total 4 columns):
 #   Column          Non-Null Count  Dtype 
---  ------          --------------  ----- 
 0   ForecastId      13459 non-null  int64 
 1   Province_State  5719 non-null   object
 2   Country_Region  13459 non-null  object
 3   Date            13459 non-null  object
dtypes: int64(1), object(3)
memory usage: 420.7+ KB


In [133]:
train.isnull().any()

Id                False
Province_State     True
Country_Region    False
Date              False
ConfirmedCases    False
Fatalities        False
dtype: bool

In [134]:
test.isnull().any()

ForecastId        False
Province_State     True
Country_Region    False
Date              False
dtype: bool

In [135]:
train['Province_State'].isnull().value_counts()

True     20700
False    15295
Name: Province_State, dtype: int64

In [136]:
train.drop(columns=['Province_State','Id'],axis=1,inplace=True)
test.drop(columns=['Province_State','ForecastId'],axis=1,inplace=True)

In [137]:
train.head()

Country_Region        Date  ConfirmedCases  Fatalities
0    Afghanistan  2020-01-22             0.0         0.0
1    Afghanistan  2020-01-23             0.0         0.0
2    Afghanistan  2020-01-24             0.0         0.0
3    Afghanistan  2020-01-25             0.0         0.0
4    Afghanistan  2020-01-26             0.0         0.0

In [138]:
test.head()

Country_Region        Date
0    Afghanistan  2020-04-02
1    Afghanistan  2020-04-03
2    Afghanistan  2020-04-04
3    Afghanistan  2020-04-05
4    Afghanistan  2020-04-06

In [139]:
train_data_by_country = train.groupby(['Date','Country_Region'],as_index=False).agg({'ConfirmedCases': 'sum', 'Fatalities': 'sum'})

In [140]:
train_data_by_country

Date      Country_Region  ConfirmedCases  Fatalities
0      2020-01-22         Afghanistan             0.0         0.0
1      2020-01-22             Albania             0.0         0.0
2      2020-01-22             Algeria             0.0         0.0
3      2020-01-22             Andorra             0.0         0.0
4      2020-01-22              Angola             0.0         0.0
...           ...                 ...             ...         ...
21155  2020-05-15             Vietnam           314.0         0.0
21156  2020-05-15  West Bank and Gaza           375.0         2.0
21157  2020-05-15      Western Sahara             6.0         0.0
21158  2020-05-15              Zambia           654.0         7.0
21159  2020-05-15            Zimbabwe            42.0         4.0

[21160 rows x 4 columns]

In [141]:
topc=["US","China","Spain",'France','United Kingdom','Italy','Brazil','Belgium','Germany','Iran','Canada']
import plotly.express as px
import plotly
plotly.offline.init_notebook_mode(connected = True)
for i in topc:
    df=train_data_by_country[train_data_by_country['Country_Region']==i]
    fig=px.line(df,x="Date",y="ConfirmedCases",title='Daily Analysis of Confirmed Cases in' + " " +i)
    fig.show()

In [142]:
for i in topc:
    df=train_data_by_country[train_data_by_country['Country_Region']==i]
    fig=px.line(df,x='Date',y='Fatalities',title='Daily Analysis of Fatalities for' + " " +i,color_discrete_map={'Fatalities':'Red'})
    fig.show()

In [143]:
#setting DatetimeIndex for train
train=train.set_index(['Date'])

In [144]:
train.head()

Country_Region  ConfirmedCases  Fatalities
Date                                                 
2020-01-22    Afghanistan             0.0         0.0
2020-01-23    Afghanistan             0.0         0.0
2020-01-24    Afghanistan             0.0         0.0
2020-01-25    Afghanistan             0.0         0.0
2020-01-26    Afghanistan             0.0         0.0

In [145]:
s=train_data_by_country['Country_Region'].tolist()

In [146]:
#generating iso3 names of the countries
import country_converter as cc
iso_alpha=cc.convert(names=s,to='ISO3')

In [147]:
#combining the codes into the dataframe train_data_by_country
train_data_by_country['iso_codes']=iso_alpha

In [148]:
train_data_by_country

Date      Country_Region  ConfirmedCases  Fatalities iso_codes
0      2020-01-22         Afghanistan             0.0         0.0       AFG
1      2020-01-22             Albania             0.0         0.0       ALB
2      2020-01-22             Algeria             0.0         0.0       DZA
3      2020-01-22             Andorra             0.0         0.0       AND
4      2020-01-22              Angola             0.0         0.0       AGO
...           ...                 ...             ...         ...       ...
21155  2020-05-15             Vietnam           314.0         0.0       VNM
21156  2020-05-15  West Bank and Gaza           375.0         2.0       PSE
21157  2020-05-15      Western Sahara             6.0         0.0       ESH
21158  2020-05-15              Zambia           654.0         7.0       ZMB
21159  2020-05-15            Zimbabwe            42.0         4.0       ZWE

[21160 rows x 5 columns]

In [149]:
#generating choropleth maps for visualizing day to day analysis of all confirmed cases around the world
train_date=train_data_by_country['Date'].astype(str)
fig_1=px.choropleth(train_data_by_country,locations='iso_codes',color='ConfirmedCases',hover_name='Country_Region',
                 hover_data=['ConfirmedCases'],animation_frame=train_date,
                  color_continuous_scale=px.colors.sequential.Purpor,title='Confirmed Cases around the world on daily basis')

fig_1.show()

In [150]:
#generating choropleth maps for visualizing day to day analysis of all fatalities around the world
train_date=train_data_by_country['Date'].astype(str)
fig_2=px.choropleth(train_data_by_country,locations='iso_codes',color='Fatalities',hover_name='Country_Region',
                 hover_data=['Fatalities'],animation_frame=train_date,
                color_continuous_scale=px.colors.sequential.PuRd,title='Fatalities around the world on daily basis')
fig_2.show()

In [151]:
#adding the date column
train['Date']=train.index

In [152]:
#removing the Datetime Index of train
train.index=g.index

In [153]:
#separating train date into day,month and year values and adding it to the train
train['Date'] = pd.to_datetime(train['Date'], errors='coerce')
train['Day'] = train['Date'].dt.strftime('%d')
train['Month'] = train['Date'].dt.strftime('%m')

In [154]:
train

Country_Region  ConfirmedCases  Fatalities       Date Day Month
0        Afghanistan             0.0         0.0 2020-01-22  22    01
1        Afghanistan             0.0         0.0 2020-01-23  23    01
2        Afghanistan             0.0         0.0 2020-01-24  24    01
3        Afghanistan             0.0         0.0 2020-01-25  25    01
4        Afghanistan             0.0         0.0 2020-01-26  26    01
...              ...             ...         ...        ...  ..   ...
35990       Zimbabwe            36.0         4.0 2020-05-11  11    05
35991       Zimbabwe            36.0         4.0 2020-05-12  12    05
35992       Zimbabwe            37.0         4.0 2020-05-13  13    05
35993       Zimbabwe            37.0         4.0 2020-05-14  14    05
35994       Zimbabwe            42.0         4.0 2020-05-15  15    05

[35995 rows x 6 columns]

In [155]:
test['Date'] = pd.to_datetime(test['Date'], errors='coerce')
test['Day'] = test['Date'].dt.strftime('%d')
test['Month'] = test['Date'].dt.strftime('%m')

In [156]:
test

Country_Region       Date Day Month
0        Afghanistan 2020-04-02  02    04
1        Afghanistan 2020-04-03  03    04
2        Afghanistan 2020-04-04  04    04
3        Afghanistan 2020-04-05  05    04
4        Afghanistan 2020-04-06  06    04
...              ...        ...  ..   ...
13454       Zimbabwe 2020-05-10  10    05
13455       Zimbabwe 2020-05-11  11    05
13456       Zimbabwe 2020-05-12  12    05
13457       Zimbabwe 2020-05-13  13    05
13458       Zimbabwe 2020-05-14  14    05

[13459 rows x 4 columns]

In [157]:
test.head()

Country_Region       Date Day Month
0    Afghanistan 2020-04-02  02    04
1    Afghanistan 2020-04-03  03    04
2    Afghanistan 2020-04-04  04    04
3    Afghanistan 2020-04-05  05    04
4    Afghanistan 2020-04-06  06    04

In [158]:
train.head()

Country_Region  ConfirmedCases  Fatalities       Date Day Month
0    Afghanistan             0.0         0.0 2020-01-22  22    01
1    Afghanistan             0.0         0.0 2020-01-23  23    01
2    Afghanistan             0.0         0.0 2020-01-24  24    01
3    Afghanistan             0.0         0.0 2020-01-25  25    01
4    Afghanistan             0.0         0.0 2020-01-26  26    01

In [159]:
del train['Date']
del test['Date']

In [160]:
#converting the independent variables into int datatype
train['ConfirmedCases'] = train['ConfirmedCases'].apply(int)
train['Fatalities'] = train['Fatalities'].apply(int)

In [161]:
cases = train.ConfirmedCases
fatalities = train.Fatalities
del train['ConfirmedCases']
del train['Fatalities']

In [162]:
#Handling Categorical data
from sklearn.preprocessing import LabelEncoder,StandardScaler
lb = LabelEncoder()
train['Country_Region'] = lb.fit_transform(train['Country_Region'])
test['Country_Region'] = lb.transform(test['Country_Region'])

In [163]:
scaler = StandardScaler()
x_train = scaler.fit_transform(train.values)
x_test = scaler.transform(test.values)

In [164]:
#using xgboost for prediction 
from sklearn.tree import DecisionTreeRegressor
from sklearn.linear_model import LinearRegression
from sklearn.ensemble import GradientBoostingRegressor
from sklearn.ensemble import VotingRegressor

In [165]:
dt=DecisionTreeRegressor(random_state=0)
lg=GradientBoostingRegressor()
lr=LinearRegression()
classifier=[('Linear Regression',lr),('DecisionTreeRegressor',dt),('GradientBoosting',lg)]

In [166]:
vc=VotingRegressor(estimators=classifier)
vc.fit(x_train,cases)

VotingRegressor(estimators=[('Linear Regression', LinearRegression()),
                            ('DecisionTreeRegressor',
                             DecisionTreeRegressor(random_state=0)),
                            ('GradientBoosting', GradientBoostingRegressor())])

In [167]:
cases_pred = vc.predict(x_test)
cases_pred

array([1188.58503861, 1229.10286008, 1280.13638845, ..., 5647.06272101,
       5685.24720915, 5723.09836395])

In [168]:
#rounding off the cases to nearest number
cases_pred = np.around(cases_pred,decimals = 0)
cases_pred

array([1189., 1229., 1280., ..., 5647., 5685., 5723.])

In [169]:
#fitting the model
vc=VotingRegressor(estimators=classifier)
vc.fit(x_train,fatalities)

VotingRegressor(estimators=[('Linear Regression', LinearRegression()),
                            ('DecisionTreeRegressor',
                             DecisionTreeRegressor(random_state=0)),
                            ('GradientBoosting', GradientBoostingRegressor())])

In [170]:
#predicting the fatalities
fatalities_pred = vc.predict(x_test)
fatalities_pred

array([ 69.73910604,  72.43422332,  77.10168772, ..., 372.27874671,
       380.28646496, 382.98158224])

In [171]:
#rounding off the Fatalities to nearest number
fatalities_pred = np.around(fatalities_pred,decimals = 0)
fatalities_pred

array([ 70.,  72.,  77., ..., 372., 380., 383.])

# Result of Prediction

In [173]:
submission.head(10)

ForecastId  ConfirmedCases  Fatalities
0           1          1189.0        70.0
1           2          1229.0        72.0
2           3          1280.0        77.0
3           4          1326.0        84.0
4           5          1386.0        90.0
5           6          1472.0        94.0
6           7          1543.0        94.0
7           8          1643.0       100.0
8           9          1749.0       108.0
9          10          1826.0       114.0

In [174]:
submission.to_csv(r"C:\Users\SAYAN\Desktop\submissionn.csv" , index = False)